# Population Density in Christchurch by Statistical area (2018 census)

In [3]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [4]:
!pip install osmnx

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 102.2/102.2 kB 2.5 MB/s eta 0:00:00


In [5]:
#import the packages required for this task

import geopandas as gpd
import folium
import numpy as np
import osmnx as ox
import matplotlib.pyplot as plt

In [6]:
#read in the shape file a gdf

shp_file_path_chch = "/content/drive/MyDrive/FinalProject/Data/Pop_Density_Data/Chch/2018-census-individual-part-1-total-new-zealand-by-statistic.shp"
gdf_chch = gpd.read_file(shp_file_path_chch)
gdf_chch = gdf_chch.to_crs('EPSG:2124')


In [7]:
# Columns to keep from the gdf
columns_to_keep = ["SA12018_V1", "C18_CURPop", "C18_CNPop", "AREA_SQ_KM", "geometry"]

# Create a subset to remove data not needed
gdf_chch = gdf_chch[columns_to_keep]

In [8]:
#create a attribute and calculate the population density in it.
#population density can be calculated by number of people / area
#for each SA1 we have calulcated the pop density
#the units for Pop_density will be people/km^2. Given the suits for AREA_ALBER are in km^2

gdf_chch['Pop_density'] = gdf_chch['C18_CURPop'] / gdf_chch['AREA_SQ_KM']

In [9]:
#Replace positive and negative infinity values with NaN in the GeoDataFrame
gdf_chch = gdf_chch.replace([np.inf, -np.inf], np.nan)

In [10]:
# Remove rows with NaN values for population and pop density
gdf_chch.dropna(subset=['Pop_density', 'C18_CURPop'], how='any', inplace=True)

In [11]:
# Set the location (Christchurch, New Zealand) to be fetched from OSM
location_chch = "Christchurch, New Zealand"

# Fetch the boundary of Christchurch city from OSM using geocode
chch_boundary = ox.geocode_to_gdf(location_chch)

#covert the crs to 2124
target_crs = "EPSG:2124"

# Change the CRS of the GeoDataFrame
chch_boundary = chch_boundary.to_crs(target_crs)

In [12]:
# Clip your GeoDataFrame to the Christchurch, New Zealand boundary
gdf_chch = gpd.overlay(gdf_chch, chch_boundary, how='intersection')

In [13]:
# Save the geodataframe as a geopackage to be used in final map visualisation

gdf_chch.to_file('/content/drive/MyDrive/FinalProject/Data/Pop_Density_Data/Chch/processed/pop_density.gpkg', driver='GPKG')

In [ ]:
# Create a Folium map centered at a specific location
map_center = [-43.50, 172.6]  # Specify the center coordinates (e.g., [latitude, longitude])
m = folium.Map(location=map_center, zoom_start=11)  # You can adjust the zoom level as needed

# Add the GeoDataFrame to the map and specify the column to use for coloring
folium.Choropleth(
    geo_data=gdf_chch,
    data=gdf_chch,
    columns=['SA12018_V1', 'Pop_density'],
    key_on="feature.properties.SA12018_V1",  # The key for the column in your GeoDataFrame
    fill_color="YlOrRd",
    fill_opacity=0.7,
    line_opacity=0.2,
    legend_name='Pop density (people per km^2)',   #Label the legend
    name='Melbourne Pop Density'  # Rename the LayerControl title here
).add_to(m)

# add the layer control to turn on/off
folium.LayerControl().add_to(m)

m

In [ ]:
# Creating make of pop density to show in report

# Define the column name to use for coloring the map
attribute_column = 'Pop_density'  # Replace with your actual attribute column name

gdf_chch.plot(column=attribute_column, legend=True)
plt.title('Christchurch SA1 Population Density (people per km^2)')
plt.savefig('Chch population_density_map.png', dpi=300, bbox_inches='tight')

plt.show()